In [84]:
import numpy
import tensorflow as tf
import sys

In [85]:
d = 50
v = 100000
w = 5
train_size = 900000
data = "umbc.casesensitive.word_pos.1M.txt"

In [109]:
word2index = {}
label2index = {}
V = {}
with open(data) as f:
    for line in f:
        line = line.rstrip("\r\n").split("\t")
        if len(line) == 2:
            word, label = line
            if word not in V:
                V[word] = 1
            else:
                V[word] += 1
            if label not in label2index:
                label2index[label] = len(label2index)
        else:
            print(line, file=sys.stderr)
V = list(map(lambda x: x[0], sorted(V.items(), key=lambda x: x[1], reverse=True)))[:v]
word2index = {x: i for i, x in enumerate(V)}
word2index["UNKNOWN"] = len(V)
V.append("UNKNOWN")
index2word = {i:w for w, i in word2index.items()}
index2label = {i:l for l, i in label2index.items()}

['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']
['<![if']


In [87]:
with open(data) as f:
    window = []
    labels = []
    train_set = []
    for _ in range(train_size):
        line = f.readline().rstrip("\r\n").split("\t")
        if len(line) == 2:
            word = word2index[line[0]] if line[0] in word2index else word2index["UNKNOWN"]
            label = label2index[line[1]]
            window.append(word)
            labels.append(label)
            if len(window) >= w:
                train_set.append(window[:w] + [labels[2]])
                window = window[1:w+1]
                labels = labels[1:w+1]
    test_set = []
    window = []
    labels = []
    for line in f:
        line = line.rstrip("\r\n").split("\t")
        if len(line) == 2:
            word = word2index[line[0]] if line[0] in word2index else word2index["UNKNOWN"]
            label = label2index[line[1]]
            window.append(word)
            labels.append(label)
            if len(window) >= w:
                test_set.append(window[:w] + [labels[2]])
                window = window[1:w+1]
                labels = labels[1:w+1]

In [88]:
print(train_set[0])
print(train_set[1])
print(train_set[2])
print(train_set[3])

[28, 15, 31676, 20056, 2512, 2]
[15, 31676, 20056, 2512, 6, 2]
[31676, 20056, 2512, 6, 92, 3]
[20056, 2512, 6, 92, 16103, 1]


In [89]:
print(len(train_set), len(test_set))

899969 99996


In [115]:
from random import shuffle
# shuffle(test_set)
# shuffle(train_set)

In [118]:
with tf.Graph().as_default():
    W = tf.Variable(numpy.random.rand(len(V), d))
    T = tf.Variable(numpy.random.rand(w, d, len(label2index)))
    b = tf.Variable(numpy.random.rand(w, len(label2index)))

    i = tf.placeholder("int32", shape=(w,))
    j = tf.placeholder("int32")

    Wi = tf.nn.embedding_lookup(W, i)
    f = tf.reduce_sum(tf.reduce_sum(tf.multiply(Wi[:, :, None], T), axis=1) + b, axis=0)
    softmax_f = tf.nn.softmax(f)
    
    optimizer = tf.train.RMSPropOptimizer(0.1)
    
    perplexity = -tf.log(softmax_f[j])
    
    update = optimizer.minimize(loss=perplexity)
    
    with tf.Session() as sess:
        sess.run(tf.global_variables_initializer())
        test_iter = iter(test_set)
        for k, train_data in enumerate(train_set):
            p, _ = sess.run([perplexity, update], feed_dict={i: train_data[:w],j: train_data[-1]})
            if k%(len(train_set)//100) == 0:
                test_data = next(test_iter)
                test_text = index2word[test_data[0]] + " " +index2word[test_data[1]]
                test_text += " " + index2word[test_data[2]] + "_" + index2label[test_data[-1]]
                test_text += " " + index2word[test_data[3]] + " " + index2word[test_data[4]]
                
                print(test_text,
                       "%f%%" % sess.run([tf.exp(-perplexity)*100], feed_dict={i: test_data[:-1],j: test_data[-1]})[0])
        variables = sess.run([W, T, b])

any affirmative way_NN that it 0.113284%
stage of cancer_NN determines which 100.000000%
over a 9-inch_JJ pie plate 0.001105%
they occupied when_WRB the suit 100.000000%
service industry is_VBZ not one 100.000000%
'' webpage was_VBD located in 100.000000%
summarised on pages_NNS 14 and 100.000000%
, such as_IN free educational 100.000000%
to pursue a_DT claim based 100.000000%
. You acknowledge_VBP that you 0.000000%


KeyboardInterrupt: 